In [1]:
from perses.analysis import utils
from openmmtools.multistate import MultiStateReporter, MultiStateSamplerAnalyzer
from simtk import unit
import os
import itertools
from tqdm import tqdm_notebook
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt


In [2]:
import logging
logger = logging.getLogger('my-logger')
logger.setLevel(logging.WARNING)
# logger.propagate = False

In [3]:
# Given a path, get dg and ddg
def analyze(path):
    reporter = MultiStateReporter(path)
    analyzer = MultiStateSamplerAnalyzer(reporter)
    f_ij, df_ij = analyzer.get_free_energy()
    f = f_ij[0,-1] # units = kT
#     f = f_ij[0,-1] * analyzer.kT
#     dg = f.in_units_of(unit.kilocalories_per_mole)
    df = df_ij[0, -1]
#     df = df_ij[0, -1] * analyzer.kT
#     ddg = df.in_units_of(unit.kilocalories_per_mole)
    return f, df

def analyze_dom(path):
    reporter = MultiStateReporter(path)
    ncfile = utils.open_netcdf(path)
    n_iterations = ncfile.variables['last_iteration'][0]
    dg, ddg = list(), list()
    for step in range (1, n_iterations + 1, 200): # add 1 because not 0-indexed
        analyzer = MultiStateSamplerAnalyzer(reporter, max_n_iterations=step)
        f_ij, df_ij = analyzer.get_free_energy()
        dg.append(f_ij[0,-1])
        ddg.append(df_ij[0,-1])
    # Get final free energy
    analyzer = MultiStateSamplerAnalyzer(reporter, max_n_iterations=n_iterations)
    f_ij, df_ij = analyzer.get_free_energy()
    dg.append(f_ij[0,-1])
    ddg.append(df_ij[0,-1])
    return np.array(dg), np.array(ddg)

### 10 ns barnase:barstar data T42A and Y29A (repex/13-15)

In [80]:
_logger = logging.getLogger()
_logger.setLevel(logging.INFO)

In [6]:
import numpy as np
for r in [25]:
    for i in tqdm_notebook(range(3)):
        print (f"dir {r} subdir {i}")
        output_dir = f'/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/'
        complex_path = os.path.join(output_dir, f"{i}_complex.nc")
#         apo_path = os.path.join(output_dir, f"{i}_apo.nc")
        print("analyzing complex")
        complex_dg, complex_ddg = analyze_dom(complex_path)
#         print("analyzing apo")
#         apo_dg, apo_ddg = analyze_dom(apo_path)
#         results = np.array([complex_dg, complex_ddg, apo_dg, apo_ddg])
        results = np.array([complex_dg, complex_ddg])
        with open(f'/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/results.npy', 'wb') as f:
            np.save(f, results)

/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/ipykernel_launcher.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  This is separate from the ipykernel package so we can avoid doing imports until


DEBUG:openmmtools.multistate.multistatereporter:Initial checkpoint file automatically chosen as /data/chodera/zhangi/perses_benchmark/repex/25/0/0_complex_checkpoint.nc
DEBUG:openmmtools.multistate.multistatereporter:checkpoint_interval != on-file checkpoint interval! Using on file analysis interval of 10.
DEBUG:openmmtools.multistate.multistatereporter:analysis_particle_indices != on-file analysis_particle_indices!Using on file analysis indices of [    0     1     2 ... 29403 29404 29405]
DEBUG:openmmtools.multistate.multistateanalyzer:Checking if we need to unbias the restraint...
DEBUG:openmmtools.multistate.multistateanalyzer:Trying to get radially symmetric restraint data...
DEBUG:openmmtools.multistate.multistateanalyzer:Retrieving end thermodynamic states...


dir 25 subdir 0
analyzing complex


DEBUG:openmmtools.multistate.multistateanalyzer:Isolating restraint force...
DEBUG:openmmtools.multistate.multistateanalyzer:No force of type <class 'openmmtools.forces.RadiallySymmetricRestraintForce'> could be found. The restraint will not be unbiased.
DEBUG:openmmtools.multistate.multistateanalyzer:Reading energies...
DEBUG:openmmtools.multistate.multistatereporter:read_replica_thermodynamic_states: iteration = [   0    1    2 ... 4998 4999 5000]
DEBUG:openmmtools.multistate.multistateanalyzer:Done.
DEBUG:openmmtools.multistate.multistateanalyzer:Assembling effective timeseries...
DEBUG:openmmtools.multistate.multistateanalyzer:Done.
DEBUG:openmmtools.multistate.multistateanalyzer:Could not find t0: None of the requested keys could be found on disk!
DEBUG:openmmtools.multistate.multistateanalyzer:Equilibration data:
DEBUG:openmmtools.multistate.multistateanalyzer: number of iterations discarded to equilibration : 1
DEBUG:openmmtools.multistate.multistateanalyzer: statistical ineffic

DEBUG:openmmtools.multistate.multistateanalyzer:   0.030   0.000   0.078   0.232   0.318   0.332   0.338   0.350   0.372   0.537   0.572
DEBUG:openmmtools.multistate.multistateanalyzer:   0.101   0.078   0.000   0.184   0.284   0.300   0.306   0.320   0.344   0.518   0.554
DEBUG:openmmtools.multistate.multistateanalyzer:   0.242   0.232   0.184   0.000   0.165   0.191   0.200   0.221   0.254   0.463   0.504
DEBUG:openmmtools.multistate.multistateanalyzer:   0.325   0.318   0.284   0.165   0.000   0.047   0.077   0.124   0.177   0.426   0.470
DEBUG:openmmtools.multistate.multistateanalyzer:   0.340   0.332   0.300   0.191   0.047   0.000   0.059   0.114   0.171   0.423   0.467
DEBUG:openmmtools.multistate.multistateanalyzer:   0.345   0.338   0.306   0.200   0.077   0.059   0.000   0.066   0.137   0.411   0.456
DEBUG:openmmtools.multistate.multistateanalyzer:   0.357   0.350   0.320   0.221   0.124   0.114   0.066   0.000   0.085   0.395   0.442
DEBUG:openmmtools.multistate.multistatean

...

DEBUG:openmmtools.multistate.multistateanalyzer:   0.094   0.093   0.085   0.062   0.031   0.029   0.017   0.000   0.020   0.040   0.096
DEBUG:openmmtools.multistate.multistateanalyzer:   0.099   0.097   0.091   0.069   0.044   0.042   0.033   0.020   0.000   0.026   0.091
DEBUG:openmmtools.multistate.multistateanalyzer:   0.106   0.104   0.098   0.079   0.057   0.056   0.050   0.040   0.026   0.000   0.079
DEBUG:openmmtools.multistate.multistateanalyzer:   0.137   0.136   0.131   0.118   0.104   0.104   0.100   0.096   0.091   0.079   0.000
DEBUG:openmmtools.multistate.multistateanalyzer:Checking if we need to unbias the restraint...
DEBUG:openmmtools.multistate.multistateanalyzer:Trying to get radially symmetric restraint data...
DEBUG:openmmtools.multistate.multistateanalyzer:Retrieving end thermodynamic states...
DEBUG:openmmtools.multistate.multistateanalyzer:Isolating restraint force...
DEBUG:openmmtools.multistate.multistateanalyzer:No force of type <class 'openmmtools.forces.Ra

DEBUG:openmmtools.multistate.multistateanalyzer:   2.126  -0.152   0.113   2.117   2.414   0.000  10.267  21.031  32.116  43.190  51.299
DEBUG:openmmtools.multistate.multistateanalyzer:  -8.141 -10.418 -10.154  -8.150  -7.852 -10.267   0.000  10.764  21.849  32.923  41.032
DEBUG:openmmtools.multistate.multistateanalyzer: -18.905 -21.182 -20.918 -18.914 -18.617 -21.031 -10.764   0.000  11.085  22.159  30.268
DEBUG:openmmtools.multistate.multistateanalyzer: -29.990 -32.268 -32.004 -29.999 -29.702 -32.116 -21.849 -11.085   0.000  11.074  19.183
DEBUG:openmmtools.multistate.multistateanalyzer: -41.064 -43.342 -43.077 -41.073 -40.776 -43.190 -32.923 -22.159 -11.074   0.000   8.109
DEBUG:openmmtools.multistate.multistateanalyzer: -49.173 -51.451 -51.186 -49.182 -48.885 -51.299 -41.032 -30.268 -19.183  -8.109   0.000
DEBUG:openmmtools.multistate.multistateanalyzer:dDeltaf_ij:
DEBUG:openmmtools.multistate.multistateanalyzer:   0.000   0.007   0.025   0.059   0.083   0.087   0.089   0.092   0.0

DEBUG:openmmtools.multistate.multistatereporter:read_replica_thermodynamic_states: iteration = [   0    1    2 ... 4998 4999 5000]
DEBUG:openmmtools.multistate.multistateanalyzer:Done.
DEBUG:openmmtools.multistate.multistateanalyzer:Assembling effective timeseries...
DEBUG:openmmtools.multistate.multistateanalyzer:Done.
DEBUG:openmmtools.multistate.multistateanalyzer:Could not find t0: None of the requested keys could be found on disk!
DEBUG:openmmtools.multistate.multistateanalyzer:Equilibration data:
DEBUG:openmmtools.multistate.multistateanalyzer: number of iterations discarded to equilibration : 1513
DEBUG:openmmtools.multistate.multistateanalyzer: statistical inefficiency of production region   : 2.5361740589141846
DEBUG:openmmtools.multistate.multistateanalyzer: effective number of uncorrelated samples        : 1060.6527099609375
DEBUG:openmmtools.multistate.multistateanalyzer:Assembling uncorrelated energies...
DEBUG:openmmtools.multistate.multistateanalyzer:Done.
DEBUG:openmmto

DEBUG:openmmtools.multistate.multistateanalyzer:   0.064   0.062   0.049   0.000   0.049   0.056   0.058   0.063   0.070   0.080   0.119
DEBUG:openmmtools.multistate.multistateanalyzer:   0.089   0.087   0.079   0.049   0.000   0.012   0.019   0.031   0.044   0.058   0.106
DEBUG:openmmtools.multistate.multistateanalyzer:   0.093   0.091   0.083   0.056   0.012   0.000   0.015   0.029   0.042   0.057   0.105
DEBUG:openmmtools.multistate.multistateanalyzer:   0.094   0.093   0.085   0.058   0.019   0.015   0.000   0.016   0.033   0.051   0.102
DEBUG:openmmtools.multistate.multistateanalyzer:   0.098   0.096   0.088   0.063   0.031   0.029   0.016   0.000   0.020   0.042   0.097
DEBUG:openmmtools.multistate.multistateanalyzer:   0.102   0.101   0.093   0.070   0.044   0.042   0.033   0.020   0.000   0.027   0.092
DEBUG:openmmtools.multistate.multistateanalyzer:   0.109   0.108   0.101   0.080   0.058   0.057   0.051   0.042   0.027   0.000   0.079
DEBUG:openmmtools.multistate.multistatean

DEBUG:openmmtools.multistate.multistateanalyzer:   2.254   0.000   0.336   2.310   2.385  -0.076  10.116  20.847  31.931  43.034  51.255
DEBUG:openmmtools.multistate.multistateanalyzer:   1.918  -0.336   0.000   1.974   2.049  -0.412   9.780  20.511  31.595  42.699  50.919
DEBUG:openmmtools.multistate.multistateanalyzer:  -0.056  -2.310  -1.974   0.000   0.075  -2.386   7.806  18.538  29.622  40.725  48.945
DEBUG:openmmtools.multistate.multistateanalyzer:  -0.131  -2.385  -2.049  -0.075   0.000  -2.461   7.732  18.463  29.547  40.650  48.870
DEBUG:openmmtools.multistate.multistateanalyzer:   2.330   0.076   0.412   2.386   2.461   0.000  10.193  20.924  32.008  43.111  51.331
DEBUG:openmmtools.multistate.multistateanalyzer:  -7.863 -10.116  -9.780  -7.806  -7.732 -10.193   0.000  10.731  21.815  32.918  41.139
DEBUG:openmmtools.multistate.multistateanalyzer: -18.594 -20.847 -20.511 -18.538 -18.463 -20.924 -10.731   0.000  11.084  22.187  30.407
DEBUG:openmmtools.multistate.multistatean

In [4]:
# Read the dicts in and compute free energies
import numpy as np
d_results = {}
for r in [25]:
    for i in tqdm_notebook(range(3)):
        with open(f"/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/results.npy", "rb") as f:
            results = np.load(f, allow_pickle=True)
            d_results[(r, i)] = results
#             print(f"{r} {i}: {results[0][-1] - results[2][-1]} ({(results[1][-1]**2 + results[3][-1]**2)**0.5}) kT")


/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/ipykernel_launcher.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """


In [20]:
# Generate replica mixing plots
titles = ['A42T']
from perses.analysis import utils
for r in [25]:
    for i in range(3):
        print (f"dir {r} subdir {i} complex")
        path = f"/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/{i}_complex.nc"
        utils.plot_replica_mixing(path, title=f"{titles[0]} complex", filename=f"{path[:-3]}_replicas.png")
        plt.clf()
#         print (f"dir {r} subdir {i} apo")
#         path = f"/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/{i}_apo.nc"
#         utils.plot_replica_mixing(path, title=f"{titles[i]} apo", filename=f"{path[:-3]}_replicas.png")
#         plt.clf()

dir 25 subdir 0 complex
dir 25 subdir 1 complex
dir 25 subdir 2 complex


<Figure size 1080x1584 with 0 Axes>

<Figure size 1080x1584 with 0 Axes>

<Figure size 1080x1584 with 0 Axes>

In [5]:
def plot_series(dg, ddg, i, phase, title):
    fig, axes = plt.subplots(nrows=2, ncols=1, sharex='col', figsize=(10,2*3), squeeze=True)
    for r in range(len(dg)):
        dg_discarded = dg[r][7:] # 7 * 200 = 1400 ps discarded
        ddg_discarded = ddg[r][7:]

        # dg
        ax = axes[0]
        x = [(j)*.2 + 1.4 for j in range(len(dg_discarded))] # *.2 bc computing energy every 200 ps,  1.4 bc discarding first 1400 ps
        y = dg_discarded
        ax.plot(x, y, color=sns.color_palette()[r])
        ax.fill_between(x, y - ddg_discarded, y + ddg_discarded, alpha=0.5)

        # ddg
        ax = axes[1]
        x = [(j)*.2 + 1.4 for j in range(len(ddg_discarded))]
        y = ddg_discarded
        ax.plot(x, y, color=sns.color_palette()[r])

#         # deviation from mean
#         ax = axes[2]
#         x = [(i)/20 + 1.5 for i in range(len(dg_discarded))]
#         y = np.array(dg_discarded) - mean # Need to the average solvent dg across replicates
#         ax.plot(x, y, color=sns.color_palette()[0])

    axes[0].set_ylabel("dG (kT)")
    axes[1].set_ylabel("ddG (kT)")
#     axes[2].set_ylabel("ddG (kT)")
    axes[1].set_xlabel("$t_{repex}$ (ns)")
    
    axes[0].set_title(f"{title} {phase}")
    plt.savefig(f"/data/chodera/zhangi/perses_benchmark/repex/25/{i}/{i}_{phase}_series.png", dpi=500)
    plt.clf()

In [6]:
#### MAKE SURE TO CHANGE PATH IN PLOT_SERIES() ####

titles = ['A42T']

# Generate dg, ddg, and discrepancy vs. time plots
for i, title in enumerate(titles):
    print(i)
    complex_dg = []
    complex_ddg = []
    apo_dg = []
    apo_ddg = []
    for r in [25]:
        for j in range(3):
            complex_dg.append(d_results[(r, j)][0])
            complex_ddg.append(d_results[(r, j)][1])
    #         apo_dg.append(d_results[(r, i)][2])
    #         apo_ddg.append(d_results[(r, i)][3])
    
#     complex_mean = np.mean([complex_dg[0][-1], complex_dg[1][-1]])
#     apo_mean = np.mean([apo_dg[0][-1], apo_dg[1][-1]]) 
    
    plot_series(complex_dg, complex_ddg, i,'complex', title)
#     plot_series(apo_dg, apo_ddg, i, 'apo', title)
    

    


0


<Figure size 720x432 with 0 Axes>

In [19]:
d_results

{(25,
  0): array([[54.53113417, 42.68144069, 42.41190462, 43.28186872, 43.76984009,
         43.96427554, 44.27447952, 44.44688411, 44.44903893, 44.58565332,
         44.57223848, 44.62637333, 44.48604301, 44.61286582, 44.28706449,
         44.38459145, 44.46380391, 44.33790476, 44.27956092, 44.14696716,
         44.41819778, 44.4581814 , 44.42487805, 44.37112813, 44.4951687 ,
         44.36083078],
        [ 7.06692619,  0.57658659,  0.42613537,  0.39003521,  0.30469903,
          0.25631732,  0.24769328,  0.22544427,  0.21062282,  0.18924749,
          0.17964755,  0.17275527,  0.17684551,  0.16873705,  0.16247255,
          0.15814071,  0.15051659,  0.14741562,  0.14384995,  0.13890241,
          0.13796341,  0.13127492,  0.12503148,  0.12321113,  0.12062924,
          0.11789232]]),
 (25,
  1): array([[46.98622619, 43.96290056, 43.81102235, 43.64276034, 43.55703771,
         43.54589365, 43.38351863, 43.08532725, 43.05795812, 43.09836202,
         43.18691099, 43.03936657, 43.0636

In [22]:
complex_dg

[array([54.53113417, 42.68144069, 42.41190462, 43.28186872, 43.76984009,
        43.96427554, 44.27447952, 44.44688411, 44.44903893, 44.58565332,
        44.57223848, 44.62637333, 44.48604301, 44.61286582, 44.28706449,
        44.38459145, 44.46380391, 44.33790476, 44.27956092, 44.14696716,
        44.41819778, 44.4581814 , 44.42487805, 44.37112813, 44.4951687 ,
        44.36083078])]

In [67]:
htf_0 = pickle.load(open("/data/chodera/zhangi/perses_benchmark/repex/12/0/0_apo.pickle", "rb" ))


In [69]:
for atom in htf_0._topology_proposal.old_topology.atoms():
    print(atom)

<Atom 0 (CH3) of chain 0 residue 0 (ACE)>
<Atom 1 (C) of chain 0 residue 0 (ACE)>
<Atom 2 (O) of chain 0 residue 0 (ACE)>
<Atom 3 (H1) of chain 0 residue 0 (ACE)>
<Atom 4 (H2) of chain 0 residue 0 (ACE)>
<Atom 5 (H3) of chain 0 residue 0 (ACE)>
<Atom 6 (N) of chain 0 residue 1 (LYS)>
<Atom 7 (CA) of chain 0 residue 1 (LYS)>
<Atom 8 (C) of chain 0 residue 1 (LYS)>
<Atom 9 (O) of chain 0 residue 1 (LYS)>
<Atom 10 (CB) of chain 0 residue 1 (LYS)>
<Atom 11 (CG) of chain 0 residue 1 (LYS)>
<Atom 12 (CD) of chain 0 residue 1 (LYS)>
<Atom 13 (CE) of chain 0 residue 1 (LYS)>
<Atom 14 (NZ) of chain 0 residue 1 (LYS)>
<Atom 15 (H2) of chain 0 residue 1 (LYS)>
<Atom 16 (HA) of chain 0 residue 1 (LYS)>
<Atom 17 (HB3) of chain 0 residue 1 (LYS)>
<Atom 18 (HB2) of chain 0 residue 1 (LYS)>
<Atom 19 (HG2) of chain 0 residue 1 (LYS)>
<Atom 20 (HG3) of chain 0 residue 1 (LYS)>
<Atom 21 (HD2) of chain 0 residue 1 (LYS)>
<Atom 22 (HD3) of chain 0 residue 1 (LYS)>
<Atom 23 (HE3) of chain 0 residue 1 (LYS)>

<Atom 2745 (H2) of chain 2 residue 525 (HOH)>
<Atom 2746 (O) of chain 2 residue 526 (HOH)>
<Atom 2747 (H1) of chain 2 residue 526 (HOH)>
<Atom 2748 (H2) of chain 2 residue 526 (HOH)>
<Atom 2749 (O) of chain 2 residue 527 (HOH)>
<Atom 2750 (H1) of chain 2 residue 527 (HOH)>
<Atom 2751 (H2) of chain 2 residue 527 (HOH)>
<Atom 2752 (O) of chain 2 residue 528 (HOH)>
<Atom 2753 (H1) of chain 2 residue 528 (HOH)>
<Atom 2754 (H2) of chain 2 residue 528 (HOH)>
<Atom 2755 (O) of chain 2 residue 529 (HOH)>
<Atom 2756 (H1) of chain 2 residue 529 (HOH)>
<Atom 2757 (H2) of chain 2 residue 529 (HOH)>
<Atom 2758 (O) of chain 2 residue 530 (HOH)>
<Atom 2759 (H1) of chain 2 residue 530 (HOH)>
<Atom 2760 (H2) of chain 2 residue 530 (HOH)>
<Atom 2761 (O) of chain 2 residue 531 (HOH)>
<Atom 2762 (H1) of chain 2 residue 531 (HOH)>
<Atom 2763 (H2) of chain 2 residue 531 (HOH)>
<Atom 2764 (O) of chain 2 residue 532 (HOH)>
<Atom 2765 (H1) of chain 2 residue 532 (HOH)>
<Atom 2766 (H2) of chain 2 residue 532 (H

<Atom 5744 (H1) of chain 2 residue 1525 (HOH)>
<Atom 5745 (H2) of chain 2 residue 1525 (HOH)>
<Atom 5746 (O) of chain 2 residue 1526 (HOH)>
<Atom 5747 (H1) of chain 2 residue 1526 (HOH)>
<Atom 5748 (H2) of chain 2 residue 1526 (HOH)>
<Atom 5749 (O) of chain 2 residue 1527 (HOH)>
<Atom 5750 (H1) of chain 2 residue 1527 (HOH)>
<Atom 5751 (H2) of chain 2 residue 1527 (HOH)>
<Atom 5752 (O) of chain 2 residue 1528 (HOH)>
<Atom 5753 (H1) of chain 2 residue 1528 (HOH)>
<Atom 5754 (H2) of chain 2 residue 1528 (HOH)>
<Atom 5755 (O) of chain 2 residue 1529 (HOH)>
<Atom 5756 (H1) of chain 2 residue 1529 (HOH)>
<Atom 5757 (H2) of chain 2 residue 1529 (HOH)>
<Atom 5758 (O) of chain 2 residue 1530 (HOH)>
<Atom 5759 (H1) of chain 2 residue 1530 (HOH)>
<Atom 5760 (H2) of chain 2 residue 1530 (HOH)>
<Atom 5761 (O) of chain 2 residue 1531 (HOH)>
<Atom 5762 (H1) of chain 2 residue 1531 (HOH)>
<Atom 5763 (H2) of chain 2 residue 1531 (HOH)>
<Atom 5764 (O) of chain 2 residue 1532 (HOH)>
<Atom 5765 (H1) of c

<Atom 9744 (H2) of chain 2 residue 2858 (HOH)>
<Atom 9745 (O) of chain 2 residue 2859 (HOH)>
<Atom 9746 (H1) of chain 2 residue 2859 (HOH)>
<Atom 9747 (H2) of chain 2 residue 2859 (HOH)>
<Atom 9748 (O) of chain 2 residue 2860 (HOH)>
<Atom 9749 (H1) of chain 2 residue 2860 (HOH)>
<Atom 9750 (H2) of chain 2 residue 2860 (HOH)>
<Atom 9751 (O) of chain 2 residue 2861 (HOH)>
<Atom 9752 (H1) of chain 2 residue 2861 (HOH)>
<Atom 9753 (H2) of chain 2 residue 2861 (HOH)>
<Atom 9754 (O) of chain 2 residue 2862 (HOH)>
<Atom 9755 (H1) of chain 2 residue 2862 (HOH)>
<Atom 9756 (H2) of chain 2 residue 2862 (HOH)>
<Atom 9757 (O) of chain 2 residue 2863 (HOH)>
<Atom 9758 (H1) of chain 2 residue 2863 (HOH)>
<Atom 9759 (H2) of chain 2 residue 2863 (HOH)>
<Atom 9760 (O) of chain 2 residue 2864 (HOH)>
<Atom 9761 (H1) of chain 2 residue 2864 (HOH)>
<Atom 9762 (H2) of chain 2 residue 2864 (HOH)>
<Atom 9763 (O) of chain 2 residue 2865 (HOH)>
<Atom 9764 (H1) of chain 2 residue 2865 (HOH)>
<Atom 9765 (H2) of c

<Atom 13743 (H2) of chain 2 residue 4191 (HOH)>
<Atom 13744 (O) of chain 2 residue 4192 (HOH)>
<Atom 13745 (H1) of chain 2 residue 4192 (HOH)>
<Atom 13746 (H2) of chain 2 residue 4192 (HOH)>
<Atom 13747 (O) of chain 2 residue 4193 (HOH)>
<Atom 13748 (H1) of chain 2 residue 4193 (HOH)>
<Atom 13749 (H2) of chain 2 residue 4193 (HOH)>
<Atom 13750 (O) of chain 2 residue 4194 (HOH)>
<Atom 13751 (H1) of chain 2 residue 4194 (HOH)>
<Atom 13752 (H2) of chain 2 residue 4194 (HOH)>
<Atom 13753 (O) of chain 2 residue 4195 (HOH)>
<Atom 13754 (H1) of chain 2 residue 4195 (HOH)>
<Atom 13755 (H2) of chain 2 residue 4195 (HOH)>
<Atom 13756 (O) of chain 2 residue 4196 (HOH)>
<Atom 13757 (H1) of chain 2 residue 4196 (HOH)>
<Atom 13758 (H2) of chain 2 residue 4196 (HOH)>
<Atom 13759 (O) of chain 2 residue 4197 (HOH)>
<Atom 13760 (H1) of chain 2 residue 4197 (HOH)>
<Atom 13761 (H2) of chain 2 residue 4197 (HOH)>
<Atom 13762 (O) of chain 2 residue 4198 (HOH)>
<Atom 13763 (H1) of chain 2 residue 4198 (HOH)>

In [72]:
htf_1 = pickle.load(open("/data/chodera/zhangi/perses_benchmark/repex/12/1/1_apo.pickle", "rb" ))


In [74]:
for atom in htf_1._topology_proposal.old_topology.atoms():
    print(atom)

<Atom 0 (CH3) of chain 0 residue 0 (ACE)>
<Atom 1 (C) of chain 0 residue 0 (ACE)>
<Atom 2 (O) of chain 0 residue 0 (ACE)>
<Atom 3 (H1) of chain 0 residue 0 (ACE)>
<Atom 4 (H2) of chain 0 residue 0 (ACE)>
<Atom 5 (H3) of chain 0 residue 0 (ACE)>
<Atom 6 (N) of chain 0 residue 1 (LYS)>
<Atom 7 (CA) of chain 0 residue 1 (LYS)>
<Atom 8 (C) of chain 0 residue 1 (LYS)>
<Atom 9 (O) of chain 0 residue 1 (LYS)>
<Atom 10 (CB) of chain 0 residue 1 (LYS)>
<Atom 11 (CG) of chain 0 residue 1 (LYS)>
<Atom 12 (CD) of chain 0 residue 1 (LYS)>
<Atom 13 (CE) of chain 0 residue 1 (LYS)>
<Atom 14 (NZ) of chain 0 residue 1 (LYS)>
<Atom 15 (H2) of chain 0 residue 1 (LYS)>
<Atom 16 (HA) of chain 0 residue 1 (LYS)>
<Atom 17 (HB3) of chain 0 residue 1 (LYS)>
<Atom 18 (HB2) of chain 0 residue 1 (LYS)>
<Atom 19 (HG2) of chain 0 residue 1 (LYS)>
<Atom 20 (HG3) of chain 0 residue 1 (LYS)>
<Atom 21 (HD2) of chain 0 residue 1 (LYS)>
<Atom 22 (HD3) of chain 0 residue 1 (LYS)>
<Atom 23 (HE3) of chain 0 residue 1 (LYS)>

<Atom 2877 (H2) of chain 2 residue 569 (HOH)>
<Atom 2878 (O) of chain 2 residue 570 (HOH)>
<Atom 2879 (H1) of chain 2 residue 570 (HOH)>
<Atom 2880 (H2) of chain 2 residue 570 (HOH)>
<Atom 2881 (O) of chain 2 residue 571 (HOH)>
<Atom 2882 (H1) of chain 2 residue 571 (HOH)>
<Atom 2883 (H2) of chain 2 residue 571 (HOH)>
<Atom 2884 (O) of chain 2 residue 572 (HOH)>
<Atom 2885 (H1) of chain 2 residue 572 (HOH)>
<Atom 2886 (H2) of chain 2 residue 572 (HOH)>
<Atom 2887 (O) of chain 2 residue 573 (HOH)>
<Atom 2888 (H1) of chain 2 residue 573 (HOH)>
<Atom 2889 (H2) of chain 2 residue 573 (HOH)>
<Atom 2890 (O) of chain 2 residue 574 (HOH)>
<Atom 2891 (H1) of chain 2 residue 574 (HOH)>
<Atom 2892 (H2) of chain 2 residue 574 (HOH)>
<Atom 2893 (O) of chain 2 residue 575 (HOH)>
<Atom 2894 (H1) of chain 2 residue 575 (HOH)>
<Atom 2895 (H2) of chain 2 residue 575 (HOH)>
<Atom 2896 (O) of chain 2 residue 576 (HOH)>
<Atom 2897 (H1) of chain 2 residue 576 (HOH)>
<Atom 2898 (H2) of chain 2 residue 576 (H

<Atom 5876 (H1) of chain 2 residue 1569 (HOH)>
<Atom 5877 (H2) of chain 2 residue 1569 (HOH)>
<Atom 5878 (O) of chain 2 residue 1570 (HOH)>
<Atom 5879 (H1) of chain 2 residue 1570 (HOH)>
<Atom 5880 (H2) of chain 2 residue 1570 (HOH)>
<Atom 5881 (O) of chain 2 residue 1571 (HOH)>
<Atom 5882 (H1) of chain 2 residue 1571 (HOH)>
<Atom 5883 (H2) of chain 2 residue 1571 (HOH)>
<Atom 5884 (O) of chain 2 residue 1572 (HOH)>
<Atom 5885 (H1) of chain 2 residue 1572 (HOH)>
<Atom 5886 (H2) of chain 2 residue 1572 (HOH)>
<Atom 5887 (O) of chain 2 residue 1573 (HOH)>
<Atom 5888 (H1) of chain 2 residue 1573 (HOH)>
<Atom 5889 (H2) of chain 2 residue 1573 (HOH)>
<Atom 5890 (O) of chain 2 residue 1574 (HOH)>
<Atom 5891 (H1) of chain 2 residue 1574 (HOH)>
<Atom 5892 (H2) of chain 2 residue 1574 (HOH)>
<Atom 5893 (O) of chain 2 residue 1575 (HOH)>
<Atom 5894 (H1) of chain 2 residue 1575 (HOH)>
<Atom 5895 (H2) of chain 2 residue 1575 (HOH)>
<Atom 5896 (O) of chain 2 residue 1576 (HOH)>
<Atom 5897 (H1) of c

<Atom 8876 (H1) of chain 2 residue 2569 (HOH)>
<Atom 8877 (H2) of chain 2 residue 2569 (HOH)>
<Atom 8878 (O) of chain 2 residue 2570 (HOH)>
<Atom 8879 (H1) of chain 2 residue 2570 (HOH)>
<Atom 8880 (H2) of chain 2 residue 2570 (HOH)>
<Atom 8881 (O) of chain 2 residue 2571 (HOH)>
<Atom 8882 (H1) of chain 2 residue 2571 (HOH)>
<Atom 8883 (H2) of chain 2 residue 2571 (HOH)>
<Atom 8884 (O) of chain 2 residue 2572 (HOH)>
<Atom 8885 (H1) of chain 2 residue 2572 (HOH)>
<Atom 8886 (H2) of chain 2 residue 2572 (HOH)>
<Atom 8887 (O) of chain 2 residue 2573 (HOH)>
<Atom 8888 (H1) of chain 2 residue 2573 (HOH)>
<Atom 8889 (H2) of chain 2 residue 2573 (HOH)>
<Atom 8890 (O) of chain 2 residue 2574 (HOH)>
<Atom 8891 (H1) of chain 2 residue 2574 (HOH)>
<Atom 8892 (H2) of chain 2 residue 2574 (HOH)>
<Atom 8893 (O) of chain 2 residue 2575 (HOH)>
<Atom 8894 (H1) of chain 2 residue 2575 (HOH)>
<Atom 8895 (H2) of chain 2 residue 2575 (HOH)>
<Atom 8896 (O) of chain 2 residue 2576 (HOH)>
<Atom 8897 (H1) of c

<Atom 11875 (O) of chain 2 residue 3569 (HOH)>
<Atom 11876 (H1) of chain 2 residue 3569 (HOH)>
<Atom 11877 (H2) of chain 2 residue 3569 (HOH)>
<Atom 11878 (O) of chain 2 residue 3570 (HOH)>
<Atom 11879 (H1) of chain 2 residue 3570 (HOH)>
<Atom 11880 (H2) of chain 2 residue 3570 (HOH)>
<Atom 11881 (O) of chain 2 residue 3571 (HOH)>
<Atom 11882 (H1) of chain 2 residue 3571 (HOH)>
<Atom 11883 (H2) of chain 2 residue 3571 (HOH)>
<Atom 11884 (O) of chain 2 residue 3572 (HOH)>
<Atom 11885 (H1) of chain 2 residue 3572 (HOH)>
<Atom 11886 (H2) of chain 2 residue 3572 (HOH)>
<Atom 11887 (O) of chain 2 residue 3573 (HOH)>
<Atom 11888 (H1) of chain 2 residue 3573 (HOH)>
<Atom 11889 (H2) of chain 2 residue 3573 (HOH)>
<Atom 11890 (O) of chain 2 residue 3574 (HOH)>
<Atom 11891 (H1) of chain 2 residue 3574 (HOH)>
<Atom 11892 (H2) of chain 2 residue 3574 (HOH)>
<Atom 11893 (O) of chain 2 residue 3575 (HOH)>
<Atom 11894 (H1) of chain 2 residue 3575 (HOH)>
<Atom 11895 (H2) of chain 2 residue 3575 (HOH)>

<Atom 14875 (O) of chain 2 residue 4569 (HOH)>
<Atom 14876 (H1) of chain 2 residue 4569 (HOH)>
<Atom 14877 (H2) of chain 2 residue 4569 (HOH)>
<Atom 14878 (O) of chain 2 residue 4570 (HOH)>
<Atom 14879 (H1) of chain 2 residue 4570 (HOH)>
<Atom 14880 (H2) of chain 2 residue 4570 (HOH)>
<Atom 14881 (O) of chain 2 residue 4571 (HOH)>
<Atom 14882 (H1) of chain 2 residue 4571 (HOH)>
<Atom 14883 (H2) of chain 2 residue 4571 (HOH)>
<Atom 14884 (O) of chain 2 residue 4572 (HOH)>
<Atom 14885 (H1) of chain 2 residue 4572 (HOH)>
<Atom 14886 (H2) of chain 2 residue 4572 (HOH)>
<Atom 14887 (O) of chain 2 residue 4573 (HOH)>
<Atom 14888 (H1) of chain 2 residue 4573 (HOH)>
<Atom 14889 (H2) of chain 2 residue 4573 (HOH)>
<Atom 14890 (O) of chain 2 residue 4574 (HOH)>
<Atom 14891 (H1) of chain 2 residue 4574 (HOH)>
<Atom 14892 (H2) of chain 2 residue 4574 (HOH)>
<Atom 14893 (O) of chain 2 residue 4575 (HOH)>
<Atom 14894 (H1) of chain 2 residue 4575 (HOH)>
<Atom 14895 (H2) of chain 2 residue 4575 (HOH)>

### 5 ns barnase:barstar data T42A (repex/19-21)

In [80]:
_logger = logging.getLogger()
_logger.setLevel(logging.INFO)

In [6]:
import numpy as np
for r in [19, 20, 21]:
    for i in tqdm_notebook(range(1)):
        print (f"dir {r} subdir {i}")
        output_dir = f'/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/'
        complex_path = os.path.join(output_dir, f"{i}_complex.nc")
        apo_path = os.path.join(output_dir, f"{i}_apo.nc")
        print("analyzing complex")
        complex_dg, complex_ddg = analyze_dom(complex_path)
        print("analyzing apo")
        apo_dg, apo_ddg = analyze_dom(apo_path)
        results = np.array([complex_dg, complex_ddg, apo_dg, apo_ddg])
        with open(f'/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/results.npy', 'wb') as f:
            np.save(f, results)

/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/ipykernel_launcher.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  This is separate from the ipykernel package so we can avoid doing imports until


DEBUG:openmmtools.multistate.multistatereporter:Initial checkpoint file automatically chosen as /data/chodera/zhangi/perses_benchmark/repex/19/0/0_complex_checkpoint.nc
DEBUG:openmmtools.multistate.multistatereporter:checkpoint_interval != on-file checkpoint interval! Using on file analysis interval of 10.
DEBUG:openmmtools.multistate.multistatereporter:analysis_particle_indices != on-file analysis_particle_indices!Using on file analysis indices of [    0     1     2 ... 32509 32510 32511]
DEBUG:openmmtools.multistate.multistateanalyzer:Checking if we need to unbias the restraint...
DEBUG:openmmtools.multistate.multistateanalyzer:Trying to get radially symmetric restraint data...
DEBUG:openmmtools.multistate.multistateanalyzer:Retrieving end thermodynamic states...


dir 19 subdir 0
analyzing complex


DEBUG:openmmtools.multistate.multistateanalyzer:Isolating restraint force...
DEBUG:openmmtools.multistate.multistateanalyzer:No force of type <class 'openmmtools.forces.RadiallySymmetricRestraintForce'> could be found. The restraint will not be unbiased.
DEBUG:openmmtools.multistate.multistateanalyzer:Reading energies...
DEBUG:openmmtools.multistate.multistatereporter:read_replica_thermodynamic_states: iteration = [   0    1    2 ... 4998 4999 5000]
DEBUG:openmmtools.multistate.multistateanalyzer:Done.
DEBUG:openmmtools.multistate.multistateanalyzer:Assembling effective timeseries...
DEBUG:openmmtools.multistate.multistateanalyzer:Done.
DEBUG:openmmtools.multistate.multistateanalyzer:Could not find t0: None of the requested keys could be found on disk!
DEBUG:openmmtools.multistate.multistateanalyzer:Equilibration data:
DEBUG:openmmtools.multistate.multistateanalyzer: number of iterations discarded to equilibration : 1
DEBUG:openmmtools.multistate.multistateanalyzer: statistical ineffic

DEBUG:openmmtools.multistate.multistateanalyzer:   0.034   0.000   0.032   0.066   0.100   0.129   0.150   0.220   0.344   0.443   0.468
DEBUG:openmmtools.multistate.multistateanalyzer:   0.064   0.032   0.000   0.036   0.074   0.107   0.131   0.207   0.336   0.437   0.462
DEBUG:openmmtools.multistate.multistateanalyzer:   0.093   0.066   0.036   0.000   0.040   0.077   0.105   0.191   0.326   0.429   0.455
DEBUG:openmmtools.multistate.multistateanalyzer:   0.122   0.100   0.074   0.040   0.000   0.039   0.073   0.174   0.317   0.422   0.448
DEBUG:openmmtools.multistate.multistateanalyzer:   0.148   0.129   0.107   0.077   0.039   0.000   0.040   0.161   0.309   0.417   0.443
DEBUG:openmmtools.multistate.multistateanalyzer:   0.167   0.150   0.131   0.105   0.073   0.040   0.000   0.139   0.297   0.408   0.435
DEBUG:openmmtools.multistate.multistateanalyzer:   0.231   0.220   0.207   0.191   0.174   0.161   0.139   0.000   0.214   0.351   0.382
DEBUG:openmmtools.multistate.multistatean

...

DEBUG:openmmtools.multistate.multistateanalyzer:   0.117   0.115   0.114   0.113   0.111   0.110   0.106   0.071   0.033   0.013   0.000
DEBUG:openmmtools.multistate.multistateanalyzer:Checking if we need to unbias the restraint...
DEBUG:openmmtools.multistate.multistateanalyzer:Trying to get radially symmetric restraint data...
DEBUG:openmmtools.multistate.multistateanalyzer:Retrieving end thermodynamic states...
DEBUG:openmmtools.multistate.multistateanalyzer:Isolating restraint force...
DEBUG:openmmtools.multistate.multistateanalyzer:No force of type <class 'openmmtools.forces.RadiallySymmetricRestraintForce'> could be found. The restraint will not be unbiased.
DEBUG:openmmtools.multistate.multistateanalyzer:Reading energies...
DEBUG:openmmtools.multistate.multistatereporter:read_replica_thermodynamic_states: iteration = [   0    1    2 ... 4998 4999 5000]
DEBUG:openmmtools.multistate.multistateanalyzer:Done.
DEBUG:openmmtools.multistate.multistateanalyzer:Assembling effective times

DEBUG:openmmtools.multistate.multistateanalyzer:  25.352  22.383  19.451  16.533  13.626  10.746  10.313   7.212   0.000  -5.831  -9.059
DEBUG:openmmtools.multistate.multistateanalyzer:  31.183  28.214  25.282  22.364  19.458  16.577  16.144  13.043   5.831   0.000  -3.227
DEBUG:openmmtools.multistate.multistateanalyzer:  34.410  31.441  28.509  25.591  22.685  19.805  19.372  16.271   9.059   3.227   0.000
DEBUG:openmmtools.multistate.multistateanalyzer:dDeltaf_ij:
DEBUG:openmmtools.multistate.multistateanalyzer:   0.000   0.009   0.016   0.022   0.028   0.032   0.037   0.079   0.101   0.108   0.110
DEBUG:openmmtools.multistate.multistateanalyzer:   0.009   0.000   0.008   0.015   0.021   0.027   0.032   0.077   0.099   0.106   0.108
DEBUG:openmmtools.multistate.multistateanalyzer:   0.016   0.008   0.000   0.008   0.015   0.021   0.028   0.075   0.098   0.105   0.107
DEBUG:openmmtools.multistate.multistateanalyzer:   0.022   0.015   0.008   0.000   0.008   0.015   0.023   0.073   0.0

DEBUG:openmmtools.multistate.multistateanalyzer:Equilibration data:
DEBUG:openmmtools.multistate.multistateanalyzer: number of iterations discarded to equilibration : 589
DEBUG:openmmtools.multistate.multistateanalyzer: statistical inefficiency of production region   : 2.494781255722046
DEBUG:openmmtools.multistate.multistateanalyzer: effective number of uncorrelated samples        : 1448.6240234375
DEBUG:openmmtools.multistate.multistateanalyzer:Assembling uncorrelated energies...
DEBUG:openmmtools.multistate.multistateanalyzer:Done.
DEBUG:openmmtools.multistate.multistateanalyzer:Computing free energy differences...
DEBUG:openmmtools.multistate.multistateanalyzer:Done.
DEBUG:openmmtools.multistate.multistateanalyzer:Computing covariance matrix...
DEBUG:openmmtools.multistate.multistateanalyzer:Deltaf_ij:
DEBUG:openmmtools.multistate.multistateanalyzer:   0.000  -2.979  -5.910  -8.825 -11.731 -14.614 -15.055 -18.194 -25.386 -31.205 -34.424
DEBUG:openmmtools.multistate.multistateanalyz

DEBUG:openmmtools.multistate.multistateanalyzer:   0.034   0.030   0.026   0.021   0.016   0.011   0.000   0.059   0.082   0.090   0.092
DEBUG:openmmtools.multistate.multistateanalyzer:   0.073   0.071   0.069   0.068   0.066   0.065   0.059   0.000   0.047   0.058   0.062
DEBUG:openmmtools.multistate.multistateanalyzer:   0.093   0.092   0.090   0.089   0.088   0.087   0.082   0.047   0.000   0.021   0.029
DEBUG:openmmtools.multistate.multistateanalyzer:   0.099   0.098   0.097   0.096   0.095   0.094   0.090   0.058   0.021   0.000   0.012
DEBUG:openmmtools.multistate.multistateanalyzer:   0.102   0.100   0.099   0.098   0.097   0.096   0.092   0.062   0.029   0.012   0.000
DEBUG:openmmtools.multistate.multistateanalyzer:Checking if we need to unbias the restraint...
DEBUG:openmmtools.multistate.multistateanalyzer:Trying to get radially symmetric restraint data...
DEBUG:openmmtools.multistate.multistateanalyzer:Retrieving end thermodynamic states...
DEBUG:openmmtools.multistate.multi

DEBUG:openmmtools.multistate.multistateanalyzer:  11.738   8.761   5.824   2.906   0.000  -2.886  -3.335  -6.450 -13.660 -19.499 -22.733
DEBUG:openmmtools.multistate.multistateanalyzer:  14.624  11.647   8.710   5.792   2.886   0.000  -0.449  -3.564 -10.773 -16.612 -19.847
DEBUG:openmmtools.multistate.multistateanalyzer:  15.073  12.096   9.159   6.241   3.335   0.449   0.000  -3.115 -10.324 -16.163 -19.398
DEBUG:openmmtools.multistate.multistateanalyzer:  18.188  15.211  12.274   9.356   6.450   3.564   3.115   0.000  -7.209 -13.048 -16.283
DEBUG:openmmtools.multistate.multistateanalyzer:  25.398  22.420  19.484  16.566  13.660  10.773  10.324   7.209   0.000  -5.839  -9.073
DEBUG:openmmtools.multistate.multistateanalyzer:  31.237  28.259  25.323  22.405  19.499  16.612  16.163  13.048   5.839   0.000  -3.234
DEBUG:openmmtools.multistate.multistateanalyzer:  34.471  31.494  28.557  25.639  22.733  19.847  19.398  16.283   9.073   3.234   0.000
DEBUG:openmmtools.multistate.multistatean

In [8]:
# Read the dicts in and compute free energies
import numpy as np
d_results = {}
for r in [19, 20, 21]:
    for i in tqdm_notebook(range(1)):
        with open(f"/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/results.npy", "rb") as f:
            results = np.load(f, allow_pickle=True)
            d_results[(r, i)] = results
            print(f"{r} {i}: {results[0][-1] - results[2][-1]} ({(results[1][-1]**2 + results[3][-1]**2)**0.5}) kT")


/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/ipykernel_launcher.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """


19 0: 5.8934976021358025 (0.1482168042041703) kT



20 0: 6.811828757381566 (0.17817176226704914) kT



21 0: 4.497528527642583 (0.1451906894798632) kT



In [9]:
# Generate replica mixing plots
titles = ['T42A', 'Y29A']
from perses.analysis import utils
for r in [19, 20, 21]:
    for i in range(1):
        print (f"dir {r} subdir {i} complex")
        path = f"/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/{i}_complex.nc"
        utils.plot_replica_mixing(path, title=f"{titles[i]} complex", filename=f"{path[:-3]}_replicas.png")
        plt.clf()
        print (f"dir {r} subdir {i} apo")
        path = f"/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/{i}_apo.nc"
        utils.plot_replica_mixing(path, title=f"{titles[i]} apo", filename=f"{path[:-3]}_replicas.png")
        plt.clf()

dir 19 subdir 0 complex


DEBUG:matplotlib.font_manager:findfont: Matching :family=sans-serif:style=normal:variant=normal:weight=normal:stretch=normal:size=10.0.
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmmi10' (cmmi10.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXGeneral' (STIXGeneralBol.ttf) normal normal bold normal>) = 10.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXNonUnicode' (STIXNonUni.ttf) normal normal regular normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans' (DejaVuSans-Oblique.ttf) oblique normal 400 normal>) = 1.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans Mono' (DejaVuSansMono-Bold.ttf) normal normal bold normal>) = 10.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif' (DejaVuSerif-Bold.ttf) normal normal bold normal>) = 10.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmr10' (cmr10.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplo

DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans Mono' (DejaVuSansMono-Oblique.ttf) oblique normal 400 normal>) = 11.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmex10' (cmex10.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif Display' (DejaVuSerifDisplay.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeTwoSym' (STIXSizTwoSymReg.ttf) normal normal regular normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif' (DejaVuSerif.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif' (DejaVuSerif-BoldItalic.ttf) italic normal bold normal>) = 11.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmss10' (cmss10.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXGeneral' (STIXGeneralBolIta.ttf) italic normal bold normal>) = 11.335


dir 19 subdir 0 apo
dir 20 subdir 0 complex
dir 20 subdir 0 apo
dir 21 subdir 0 complex
dir 21 subdir 0 apo


<Figure size 1080x1584 with 0 Axes>

<Figure size 1080x1584 with 0 Axes>

<Figure size 1080x1584 with 0 Axes>

<Figure size 1080x1584 with 0 Axes>

<Figure size 1080x1584 with 0 Axes>

<Figure size 1080x1584 with 0 Axes>

In [10]:
def plot_series(dg, ddg, i, phase, title):
    fig, axes = plt.subplots(nrows=2, ncols=1, sharex='col', figsize=(10,2*3), squeeze=True)
    for r in range(len(dg)):
        dg_discarded = dg[r][7:] # 7 * 200 = 1400 ps discarded
        ddg_discarded = ddg[r][7:]

        # dg
        ax = axes[0]
        x = [(j)*.2 + 1.4 for j in range(len(dg_discarded))] # *.2 bc computing energy every 200 ps,  1.4 bc discarding first 1400 ps
        y = dg_discarded
        ax.plot(x, y, color=sns.color_palette()[r])
        ax.fill_between(x, y - ddg_discarded, y + ddg_discarded, alpha=0.5)

        # ddg
        ax = axes[1]
        x = [(j)*.2 + 1.4 for j in range(len(ddg_discarded))]
        y = ddg_discarded
        ax.plot(x, y, color=sns.color_palette()[0])

#         # deviation from mean
#         ax = axes[2]
#         x = [(i)/20 + 1.5 for i in range(len(dg_discarded))]
#         y = np.array(dg_discarded) - mean # Need to the average solvent dg across replicates
#         ax.plot(x, y, color=sns.color_palette()[0])

    axes[0].set_ylabel("dG (kT)")
    axes[1].set_ylabel("ddG (kT)")
#     axes[2].set_ylabel("ddG (kT)")
    axes[1].set_xlabel("$t_{repex}$ (ns)")
    
    axes[0].set_title(f"{title} {phase}")
    plt.savefig(f"/data/chodera/zhangi/perses_benchmark/repex/19/{i}/{i}_{phase}_series.png", dpi=500)
    plt.clf()

In [11]:
#### MAKE SURE TO CHANGE PATH IN PLOT_SERIES() ####

# titles = ['T42A', 'Y29A']
titles = ['T42A']


# Generate dg, ddg, and discrepancy vs. time plots
for i, title in enumerate(titles):
    print(i)
    complex_dg = []
    complex_ddg = []
    apo_dg = []
    apo_ddg = []
    for r in [19, 20, 21]:
        complex_dg.append(d_results[(r, i)][0])
        complex_ddg.append(d_results[(r, i)][1])
        apo_dg.append(d_results[(r, i)][2])
        apo_ddg.append(d_results[(r, i)][3])
    
#     complex_mean = np.mean([complex_dg[0][-1], complex_dg[1][-1]])
#     apo_mean = np.mean([apo_dg[0][-1], apo_dg[1][-1]]) 
    
    plot_series(complex_dg, complex_ddg, i,'complex', title)
    plot_series(apo_dg, apo_ddg, i, 'apo', title)
    

    


DEBUG:matplotlib.font_manager:findfont: Matching :family=STIXGeneral:style=normal:variant=normal:weight=normal:stretch=normal:size=10.0.
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmmi10' (cmmi10.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXGeneral' (STIXGeneralBol.ttf) normal normal bold normal>) = 0.33499999999999996
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXNonUnicode' (STIXNonUni.ttf) normal normal regular normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans' (DejaVuSans-Oblique.ttf) oblique normal 400 normal>) = 11.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans Mono' (DejaVuSansMono-Bold.ttf) normal normal bold normal>) = 10.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif' (DejaVuSerif-Bold.ttf) normal normal bold normal>) = 10.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmr10' (cmr10.ttf) normal normal 400 normal>) = 10.

0


DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif Display' (DejaVuSerifDisplay.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeTwoSym' (STIXSizTwoSymReg.ttf) normal normal regular normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif' (DejaVuSerif.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif' (DejaVuSerif-BoldItalic.ttf) italic normal bold normal>) = 11.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmss10' (cmss10.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXGeneral' (STIXGeneralBolIta.ttf) italic normal bold normal>) = 1.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans Mono' (DejaVuSansMono.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeOneSym' (STIXSizOneSymReg.ttf) normal normal regular norma

DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXGeneral' (STIXGeneral.ttf) normal normal regular normal>) = 1.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeFourSym' (STIXSizFourSymBol.ttf) normal normal bold normal>) = 11.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmb10' (cmb10.ttf) normal normal 400 normal>) = 11.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeTwoSym' (STIXSizTwoSymBol.ttf) normal normal bold normal>) = 11.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXNonUnicode' (STIXNonUniIta.ttf) italic normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmtt10' (cmtt10.ttf) normal normal 400 normal>) = 11.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXNonUnicode' (STIXNonUniBolIta.ttf) italic normal bold normal>) = 10.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeFourSym' (STIXSizFourSymReg.ttf) normal normal regular normal>) = 11.05
DEBUG:matplotlib

DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXNonUnicode' (STIXNonUniBolIta.ttf) italic normal bold normal>) = 1.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeFourSym' (STIXSizFourSymReg.ttf) normal normal regular normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXGeneral' (STIXGeneralItalic.ttf) italic normal 400 normal>) = 11.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans' (DejaVuSans-Bold.ttf) normal normal bold normal>) = 10.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXNonUnicode' (STIXNonUniBol.ttf) normal normal bold normal>) = 0.33499999999999996
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeThreeSym' (STIXSizThreeSymReg.ttf) normal normal regular normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans Mono' (DejaVuSansMono-BoldOblique.ttf) oblique normal bold normal>) = 11.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeFiveSym' (ST

...

DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeFourSym' (STIXSizFourSymBol.ttf) normal normal bold normal>) = 11.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmb10' (cmb10.ttf) normal normal 400 normal>) = 11.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeTwoSym' (STIXSizTwoSymBol.ttf) normal normal bold normal>) = 11.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXNonUnicode' (STIXNonUniIta.ttf) italic normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmtt10' (cmtt10.ttf) normal normal 400 normal>) = 11.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXNonUnicode' (STIXNonUniBolIta.ttf) italic normal bold normal>) = 10.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeFourSym' (STIXSizFourSymReg.ttf) normal normal regular normal>) = 11.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXGeneral' (STIXGeneralItalic.ttf) italic normal 400 normal>) = 10.05
DEBUG:matplot

DEBUG:matplotlib.font_manager:findfont: Matching :family=DejaVu Sans Mono:style=normal:variant=normal:weight=normal:stretch=normal:size=10.0.
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmmi10' (cmmi10.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXGeneral' (STIXGeneralBol.ttf) normal normal bold normal>) = 10.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXNonUnicode' (STIXNonUni.ttf) normal normal regular normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans' (DejaVuSans-Oblique.ttf) oblique normal 400 normal>) = 11.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans Mono' (DejaVuSansMono-Bold.ttf) normal normal bold normal>) = 0.33499999999999996
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif' (DejaVuSerif-Bold.ttf) normal normal bold normal>) = 10.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmr10' (cmr10.ttf) normal normal 400 normal>) 

DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Sans Mono' (DejaVuSansMono-Oblique.ttf) oblique normal 400 normal>) = 11.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmex10' (cmex10.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif Display' (DejaVuSerifDisplay.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXSizeTwoSym' (STIXSizTwoSymReg.ttf) normal normal regular normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif' (DejaVuSerif.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'DejaVu Serif' (DejaVuSerif-BoldItalic.ttf) italic normal bold normal>) = 11.335
DEBUG:matplotlib.font_manager:findfont: score(<Font 'cmss10' (cmss10.ttf) normal normal 400 normal>) = 10.05
DEBUG:matplotlib.font_manager:findfont: score(<Font 'STIXGeneral' (STIXGeneralBolIta.ttf) italic normal bold normal>) = 11.335


<Figure size 720x432 with 0 Axes>

<Figure size 720x432 with 0 Axes>

### 2.5 ns barnase:barstar data T42A (repex/22-23)

In [80]:
_logger = logging.getLogger()
_logger.setLevel(logging.INFO)

In [12]:
import numpy as np
for r in [22, 23, 24]:
    for i in tqdm_notebook(range(1)):
        print (f"dir {r} subdir {i}")
        output_dir = f'/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/'
        complex_path = os.path.join(output_dir, f"{i}_complex.nc")
        apo_path = os.path.join(output_dir, f"{i}_apo.nc")
        print("analyzing complex")
        complex_dg, complex_ddg = analyze_dom(complex_path)
        print("analyzing apo")
        apo_dg, apo_ddg = analyze_dom(apo_path)
        results = np.array([complex_dg, complex_ddg, apo_dg, apo_ddg])
        with open(f'/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/results.npy', 'wb') as f:
            np.save(f, results)

/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/ipykernel_launcher.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  This is separate from the ipykernel package so we can avoid doing imports until


DEBUG:openmmtools.multistate.multistatereporter:Initial checkpoint file automatically chosen as /data/chodera/zhangi/perses_benchmark/repex/22/0/0_complex_checkpoint.nc


dir 22 subdir 0
analyzing complex


DEBUG:openmmtools.multistate.multistatereporter:checkpoint_interval != on-file checkpoint interval! Using on file analysis interval of 10.
DEBUG:openmmtools.multistate.multistatereporter:analysis_particle_indices != on-file analysis_particle_indices!Using on file analysis indices of [    0     1     2 ... 32509 32510 32511]
DEBUG:openmmtools.multistate.multistateanalyzer:Checking if we need to unbias the restraint...
DEBUG:openmmtools.multistate.multistateanalyzer:Trying to get radially symmetric restraint data...
DEBUG:openmmtools.multistate.multistateanalyzer:Retrieving end thermodynamic states...
DEBUG:openmmtools.multistate.multistateanalyzer:Isolating restraint force...
DEBUG:openmmtools.multistate.multistateanalyzer:No force of type <class 'openmmtools.forces.RadiallySymmetricRestraintForce'> could be found. The restraint will not be unbiased.
DEBUG:openmmtools.multistate.multistateanalyzer:Reading energies...
DEBUG:openmmtools.multistate.multistatereporter:read_replica_thermodyn

DEBUG:openmmtools.multistate.multistateanalyzer:   0.748   0.600   0.454   0.304   0.152   0.000   0.148   0.294   0.434   0.565   0.702   0.770   0.760   0.754   0.752   0.777   0.881   1.006   1.092   1.148   1.180   1.193
DEBUG:openmmtools.multistate.multistateanalyzer:   0.844   0.710   0.576   0.439   0.295   0.148   0.000   0.151   0.298   0.441   0.595   0.672   0.661   0.654   0.653   0.682   0.799   0.935   1.027   1.086   1.120   1.133
DEBUG:openmmtools.multistate.multistateanalyzer:   0.929   0.808   0.687   0.562   0.431   0.294   0.151   0.000   0.152   0.305   0.479   0.569   0.557   0.549   0.548   0.584   0.718   0.867   0.965   1.028   1.063   1.078
DEBUG:openmmtools.multistate.multistateanalyzer:   1.009   0.898   0.789   0.677   0.559   0.434   0.298   0.152   0.000   0.161   0.358   0.461   0.450   0.443   0.444   0.491   0.645   0.808   0.912   0.979   1.016   1.031
DEBUG:openmmtools.multistate.multistateanalyzer:   1.085   0.982   0.884   0.783   0.678   0.565   0

...

DEBUG:openmmtools.multistate.multistateanalyzer:Computing covariance matrix...
DEBUG:openmmtools.multistate.multistateanalyzer:Deltaf_ij:
DEBUG:openmmtools.multistate.multistateanalyzer:   0.000  -3.229  -6.460  -9.722 -13.040 -16.406 -19.788 -23.153 -26.529 -30.165 -34.410 -35.997 -34.667 -33.578 -33.063 -33.290 -34.120 -35.005 -35.444 -35.254 -34.489 -33.282
DEBUG:openmmtools.multistate.multistateanalyzer:   3.229   0.000  -3.231  -6.494  -9.811 -13.178 -16.560 -19.925 -23.301 -26.936 -31.182 -32.768 -31.439 -30.349 -29.834 -30.061 -30.891 -31.776 -32.215 -32.026 -31.260 -30.053
DEBUG:openmmtools.multistate.multistateanalyzer:   6.460   3.231   0.000  -3.263  -6.580  -9.947 -13.329 -16.694 -20.070 -23.705 -27.951 -29.537 -28.208 -27.118 -26.603 -26.830 -27.660 -28.545 -28.984 -28.795 -28.029 -26.822
DEBUG:openmmtools.multistate.multistateanalyzer:   9.722   6.494   3.263   0.000  -3.318  -6.684 -10.066 -13.431 -16.807 -20.443 -24.688 -26.274 -24.945 -23.856 -23.341 -23.568 -24.398 -2

DEBUG:openmmtools.multistate.multistateanalyzer:   0.088   0.084   0.080   0.077   0.073   0.069   0.065   0.062   0.056   0.042   0.031   0.029   0.026   0.018   0.000   0.026   0.048   0.060   0.066   0.069   0.070   0.071
DEBUG:openmmtools.multistate.multistateanalyzer:   0.096   0.092   0.089   0.086   0.082   0.079   0.076   0.073   0.068   0.057   0.049   0.047   0.046   0.040   0.026   0.000   0.027   0.043   0.051   0.054   0.056   0.057
DEBUG:openmmtools.multistate.multistateanalyzer:   0.105   0.102   0.099   0.096   0.093   0.090   0.087   0.084   0.080   0.071   0.065   0.064   0.063   0.058   0.048   0.027   0.000   0.020   0.030   0.036   0.038   0.040
DEBUG:openmmtools.multistate.multistateanalyzer:   0.111   0.108   0.105   0.103   0.100   0.097   0.094   0.092   0.088   0.080   0.075   0.074   0.073   0.069   0.060   0.043   0.020   0.000   0.012   0.019   0.023   0.025
DEBUG:openmmtools.multistate.multistateanalyzer:   0.114   0.112   0.109   0.106   0.103   0.101   0

DEBUG:openmmtools.multistate.multistateanalyzer:  34.431  31.223  28.002  24.744  21.436  18.087  14.729  11.385   8.013   4.345   0.067  -1.523  -0.197   0.879   1.395   1.185   0.379  -0.511  -0.959  -0.769   0.000   1.210
DEBUG:openmmtools.multistate.multistateanalyzer:  33.221  30.013  26.792  23.534  20.226  16.877  13.519  10.175   6.803   3.135  -1.143  -2.733  -1.407  -0.331   0.185  -0.025  -0.831  -1.721  -2.169  -1.979  -1.210   0.000
DEBUG:openmmtools.multistate.multistateanalyzer:dDeltaf_ij:
DEBUG:openmmtools.multistate.multistateanalyzer:   0.000   0.012   0.021   0.030   0.037   0.043   0.048   0.052   0.056   0.064   0.073   0.076   0.076   0.078   0.081   0.088   0.097   0.103   0.106   0.107   0.108   0.109
DEBUG:openmmtools.multistate.multistateanalyzer:   0.012   0.000   0.011   0.020   0.029   0.036   0.042   0.047   0.051   0.059   0.069   0.072   0.073   0.074   0.078   0.085   0.094   0.100   0.103   0.105   0.106   0.106
DEBUG:openmmtools.multistate.multistatea

DEBUG:openmmtools.multistate.multistateanalyzer:  13.065   9.835   6.592   3.317   0.000  -3.348  -6.705 -10.054 -13.435 -17.111 -21.406 -23.006 -21.683 -20.595 -20.066 -20.313 -21.169 -22.053 -22.483 -22.282 -21.507 -20.292
DEBUG:openmmtools.multistate.multistateanalyzer:  16.413  13.183   9.940   6.665   3.348   0.000  -3.357  -6.706 -10.086 -13.763 -18.057 -19.658 -18.335 -17.247 -16.718 -16.965 -17.821 -18.705 -19.135 -18.934 -18.159 -16.944
DEBUG:openmmtools.multistate.multistateanalyzer:  19.770  16.540  13.297  10.022   6.705   3.357   0.000  -3.349  -6.730 -10.406 -14.701 -16.301 -14.978 -13.890 -13.361 -13.608 -14.464 -15.348 -15.778 -15.577 -14.802 -13.587
DEBUG:openmmtools.multistate.multistateanalyzer:  23.119  19.889  16.646  13.371  10.054   6.706   3.349   0.000  -3.381  -7.058 -11.352 -12.953 -11.630 -10.542 -10.013 -10.259 -11.115 -12.000 -12.429 -12.229 -11.453 -10.238
DEBUG:openmmtools.multistate.multistateanalyzer:  26.500  23.270  20.027  16.752  13.435  10.086   6

DEBUG:openmmtools.multistate.multistateanalyzer:   0.109   0.106   0.104   0.101   0.099   0.096   0.094   0.092   0.088   0.081   0.077   0.076   0.075   0.072   0.065   0.050   0.033   0.018   0.007   0.000   0.004   0.007
DEBUG:openmmtools.multistate.multistateanalyzer:   0.109   0.107   0.104   0.102   0.100   0.097   0.095   0.093   0.089   0.082   0.078   0.077   0.076   0.073   0.066   0.052   0.035   0.021   0.011   0.004   0.000   0.003
DEBUG:openmmtools.multistate.multistateanalyzer:   0.110   0.107   0.105   0.102   0.100   0.098   0.096   0.093   0.090   0.083   0.078   0.078   0.077   0.074   0.067   0.053   0.037   0.023   0.014   0.007   0.003   0.000


In [13]:
# Read the dicts in and compute free energies
import numpy as np
d_results = {}
for r in [22, 23, 24]:
    for i in tqdm_notebook(range(1)):
        with open(f"/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/results.npy", "rb") as f:
            results = np.load(f, allow_pickle=True)
            d_results[(r, i)] = results
            print(f"{r} {i}: {results[0][-1] - results[2][-1]} ({(results[1][-1]**2 + results[3][-1]**2)**0.5}) kT")


/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/ipykernel_launcher.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """


22 0: 7.4589591657124785 (0.18406639583927875) kT



23 0: 8.708048631511797 (0.23235967832759916) kT



24 0: 5.977592419522484 (0.16828969028144974) kT



In [14]:
# Generate replica mixing plots
titles = ['T42A', 'Y29A']
from perses.analysis import utils
for r in [22, 23, 24]:
    for i in range(1):
        print (f"dir {r} subdir {i} complex")
        path = f"/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/{i}_complex.nc"
        utils.plot_replica_mixing(path, title=f"{titles[i]} complex", filename=f"{path[:-3]}_replicas.png")
        plt.clf()
        print (f"dir {r} subdir {i} apo")
        path = f"/data/chodera/zhangi/perses_benchmark/repex/{r}/{i}/{i}_apo.nc"
        utils.plot_replica_mixing(path, title=f"{titles[i]} apo", filename=f"{path[:-3]}_replicas.png")
        plt.clf()

dir 22 subdir 0 complex
dir 22 subdir 0 apo
dir 23 subdir 0 complex
dir 23 subdir 0 apo
dir 24 subdir 0 complex
dir 24 subdir 0 apo


<Figure size 1080x3168 with 0 Axes>

<Figure size 1080x3168 with 0 Axes>

<Figure size 1080x3168 with 0 Axes>

<Figure size 1080x3168 with 0 Axes>

<Figure size 1080x3168 with 0 Axes>

<Figure size 1080x3168 with 0 Axes>

In [15]:
def plot_series(dg, ddg, i, phase, title):
    fig, axes = plt.subplots(nrows=2, ncols=1, sharex='col', figsize=(10,2*3), squeeze=True)
    for r in range(len(dg)):
        dg_discarded = dg[r][7:] # 7 * 200 = 1400 ps discarded
        ddg_discarded = ddg[r][7:]

        # dg
        ax = axes[0]
        x = [(j)*.2 + 1.4 for j in range(len(dg_discarded))] # *.2 bc computing energy every 200 ps,  1.4 bc discarding first 1400 ps
        y = dg_discarded
        ax.plot(x, y, color=sns.color_palette()[r])
        ax.fill_between(x, y - ddg_discarded, y + ddg_discarded, alpha=0.5)

        # ddg
        ax = axes[1]
        x = [(j)*.2 + 1.4 for j in range(len(ddg_discarded))]
        y = ddg_discarded
        ax.plot(x, y, color=sns.color_palette()[0])

#         # deviation from mean
#         ax = axes[2]
#         x = [(i)/20 + 1.5 for i in range(len(dg_discarded))]
#         y = np.array(dg_discarded) - mean # Need to the average solvent dg across replicates
#         ax.plot(x, y, color=sns.color_palette()[0])

    axes[0].set_ylabel("dG (kT)")
    axes[1].set_ylabel("ddG (kT)")
#     axes[2].set_ylabel("ddG (kT)")
    axes[1].set_xlabel("$t_{repex}$ (ns)")
    
    axes[0].set_title(f"{title} {phase}")
    plt.savefig(f"/data/chodera/zhangi/perses_benchmark/repex/22/{i}/{i}_{phase}_series.png", dpi=500)
    plt.clf()

In [17]:
#### MAKE SURE TO CHANGE PATH IN PLOT_SERIES() ####

titles = ['T42A', 'Y29A']

# Generate dg, ddg, and discrepancy vs. time plots
complex_dg = []
complex_ddg = []
apo_dg = []
apo_ddg = []
for r in [22, 23, 24]:
    complex_dg.append(d_results[(r, i)][0])
    complex_ddg.append(d_results[(r, i)][1])
    apo_dg.append(d_results[(r, i)][2])
    apo_ddg.append(d_results[(r, i)][3])

#     complex_mean = np.mean([complex_dg[0][-1], complex_dg[1][-1]])
#     apo_mean = np.mean([apo_dg[0][-1], apo_dg[1][-1]]) 

plot_series(complex_dg, complex_ddg, 0,'complex', titles[0])
plot_series(apo_dg, apo_ddg, 0, 'apo', titles[0])
    

    


<Figure size 720x432 with 0 Axes>

<Figure size 720x432 with 0 Axes>